# PARTIE 4 : ANIMATION - ÉVOLUTION S&P 500

Création d'animations pour visualiser l'évolution temporelle du S&P 500

In [12]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import yfinance as yf
from datetime import datetime, timedelta
import matplotlib.animation as animation
from IPython.display import HTML
import warnings
warnings.filterwarnings('ignore')

plt.style.use('seaborn-v0_8-darkgrid')
sns.set_palette("Set3")
%matplotlib inline

In [13]:
# Définir le dossier de sortie
import os
output_dir = r"C:\Users\USER\Desktop\bachelor-3-ece\Visualisation\TP6\sp500_python"
os.makedirs(output_dir, exist_ok=True)
print(f"Les GIFs seront sauvegardés dans : {output_dir}")

Les GIFs seront sauvegardés dans : C:\Users\USER\Desktop\bachelor-3-ece\Visualisation\TP6\sp500_python


In [14]:
sp500_symbols = [
    "AAPL", "MSFT", "GOOGL", "AMZN", "NVDA", "META", "TSLA", "BRK.B", "JNJ", "V",
    "WMT", "JPM", "PG", "MA", "UNH", "HD", "DIS", "CRM", "MCD", "KO",
    "NFLX", "CSCO", "PEP", "ABT", "ABBV", "MMM", "XOM", "CVX", "BA", "COST",
    "AMD", "INTC", "QCOM", "PYPL", "TXN", "ADBE", "IBM", "AVGO", "ACN", "GILD",
    "CDNS", "MRVL", "OKTA", "CCI", "ANET", "SNPS", "ASML", "NOW", "PANW", "LRCX"
]

sector_info = pd.DataFrame({
    'symbol': ["AAPL", "MSFT", "GOOGL", "AMZN", "NVDA", "META", "TSLA", "BRK.B", "JNJ", "V",
               "WMT", "JPM", "PG", "MA", "UNH", "HD", "DIS", "CRM", "MCD", "KO",
               "NFLX", "CSCO", "PEP", "ABT", "ABBV", "MMM", "XOM", "CVX", "BA", "COST",
               "AMD", "INTC", "QCOM", "PYPL", "TXN", "ADBE", "IBM", "AVGO", "ACN", "GILD",
               "CDNS", "MRVL", "OKTA", "CCI", "ANET", "SNPS", "ASML", "NOW", "PANW", "LRCX"],
    'sector': ["Technology", "Technology", "Technology", "Consumer", "Technology", "Technology", "Consumer", "Finance", "Healthcare", "Finance",
               "Consumer", "Finance", "Consumer", "Finance", "Healthcare", "Consumer", "Consumer", "Technology", "Consumer", "Consumer",
               "Technology", "Technology", "Consumer", "Healthcare", "Healthcare", "Industrial", "Energy", "Energy", "Industrial", "Consumer",
               "Technology", "Technology", "Technology", "Finance", "Technology", "Technology", "Technology", "Technology", "Technology", "Healthcare",
               "Technology", "Technology", "Technology", "Real Estate", "Technology", "Technology", "Technology", "Technology", "Technology", "Technology"]
})

In [15]:
# Récupérer les données
print("Récupération des données S&P 500...")
end_date = datetime.now()
start_date = end_date - timedelta(days=365)

# Télécharger les données
sp500_data_list = []
for symbol in sp500_symbols:
    try:
        data = yf.download(symbol, start=start_date, end=end_date, progress=False)
        if not data.empty:  # Vérifier que des données ont été récupérées
            # Aplatir les colonnes si MultiIndex
            if isinstance(data.columns, pd.MultiIndex):
                data.columns = data.columns.get_level_values(0)
            data = data.reset_index()
            data['symbol'] = symbol
            sp500_data_list.append(data)
        else:
            print(f"Aucune donnée pour {symbol}")
    except Exception as e:
        print(f"Erreur pour {symbol}: {e}")

# Concaténer les données verticalement
sp500_data = pd.concat(sp500_data_list, axis=0, ignore_index=True)

# Standardiser les noms de colonnes
sp500_data.columns = sp500_data.columns.str.lower().str.replace(' ', '_')

# Joindre les secteurs
sp500_data = sp500_data.merge(sector_info, on='symbol', how='left')

print(f"Données chargées: {len(sp500_data)} lignes")
print(f"Actions récupérées: {sp500_data['symbol'].nunique()}")

Récupération des données S&P 500...


$BRK.B: possibly delisted; no timezone found

1 Failed download:
['BRK.B']: possibly delisted; no timezone found


Aucune donnée pour BRK.B
Données chargées: 12250 lignes
Actions récupérées: 49


## ANIMATION 1 : Évolution du prix des Top 10 stocks

In [16]:
top_10_symbols = ["AAPL", "MSFT", "GOOGL", "AMZN", "NVDA", "META", "TSLA", "BRK.B", "JNJ", "V"]

top_10_data = sp500_data[sp500_data['symbol'].isin(top_10_symbols)].copy()
top_10_data = top_10_data.sort_values('date')

# Filter to only symbols that have data
available_symbols = top_10_data['symbol'].unique().tolist()
top_10_symbols = [s for s in top_10_symbols if s in available_symbols]
print(f"Symbols with data: {top_10_symbols}")

# Calculer le prix normalisé
for symbol in top_10_symbols:
    mask = top_10_data['symbol'] == symbol
    first_price = top_10_data[mask].iloc[0]['close']
    top_10_data.loc[mask, 'normalized_price'] = (top_10_data.loc[mask, 'close'] / first_price) * 100

# Obtenir les dates uniques et échantillonner
unique_dates = sorted(top_10_data['date'].unique())
sampled_dates = unique_dates[::7]  # Prendre une date sur 7 pour réduire le nombre de frames

fig, ax = plt.subplots(figsize=(12, 6))

def animate_price_evolution(frame):
    ax.clear()
    current_date = sampled_dates[frame]
    data_until_now = top_10_data[top_10_data['date'] <= current_date]
    
    # Grouper par symbole et obtenir les statistiques
    boxplot_data = [data_until_now[data_until_now['symbol'] == sym]['close'].values 
                    for sym in top_10_symbols]
    
    sectors = [sector_info[sector_info['symbol'] == sym]['sector'].values[0] for sym in top_10_symbols]
    colors_map = {'Technology': '#8dd3c7', 'Consumer': '#ffffb3', 'Finance': '#bebada', 
                  'Healthcare': '#fb8072', 'Industrial': '#80b1d3'}
    colors = [colors_map.get(s, '#fdb462') for s in sectors]
    
    bp = ax.boxplot(boxplot_data, labels=top_10_symbols, patch_artist=True)
    for patch, color in zip(bp['boxes'], colors):
        patch.set_facecolor(color)
        patch.set_alpha(0.7)
    
    ax.set_xlabel('Symbole', fontsize=12)
    ax.set_ylabel('Prix (USD)', fontsize=12)
    ax.set_title(f'Évolution du prix - Période: {current_date.strftime("%Y-%m-%d")}', 
                 fontsize=14, fontweight='bold')
    ax.tick_params(axis='x', rotation=45)
    plt.tight_layout()

anim1 = animation.FuncAnimation(fig, animate_price_evolution, frames=len(sampled_dates), 
                                interval=100, repeat=True)

# Sauvegarder l'animation
print("Création de l'animation 1...")
anim1.save(os.path.join(output_dir, 'sp500_price_evolution.gif'), writer='pillow', fps=10)
plt.close()

print("Animation 1 créée : sp500_price_evolution.gif")
HTML(anim1.to_jshtml())

Symbols with data: ['AAPL', 'MSFT', 'GOOGL', 'AMZN', 'NVDA', 'META', 'TSLA', 'JNJ', 'V']
Création de l'animation 1...
Animation 1 créée : sp500_price_evolution.gif


<Figure size 640x480 with 0 Axes>

## ANIMATION 2 : Évolution cumulée du prix par secteur

In [17]:
# Calculer le changement de prix par rapport au début
sp500_data_sorted = sp500_data.sort_values(['symbol', 'date'])
for symbol in sp500_data_sorted['symbol'].unique():
    mask = sp500_data_sorted['symbol'] == symbol
    symbol_data = sp500_data_sorted[mask]
    if len(symbol_data) > 0:
        first_price = symbol_data.iloc[0]['close']
        sp500_data_sorted.loc[mask, 'price_change_pct'] = ((sp500_data_sorted.loc[mask, 'close'] - first_price) / first_price) * 100

sector_cumulative = sp500_data_sorted.groupby(['date', 'sector'])['price_change_pct'].mean().reset_index()
sector_cumulative.columns = ['date', 'sector', 'avg_change']
sector_cumulative = sector_cumulative.sort_values('date')

# Échantillonner les dates
unique_dates_sec = sorted(sector_cumulative['date'].unique())
sampled_dates_sec = unique_dates_sec[::7]

fig2, ax2 = plt.subplots(figsize=(12, 6))

def animate_sector_change(frame):
    ax2.clear()
    current_date = sampled_dates_sec[frame]
    data_at_date = sector_cumulative[sector_cumulative['date'] == current_date].sort_values('avg_change')
    
    colors = plt.cm.Set3(range(len(data_at_date)))
    ax2.barh(data_at_date['sector'], data_at_date['avg_change'], color=colors, alpha=0.8)
    ax2.set_xlabel('Changement (%)', fontsize=12)
    ax2.set_ylabel('Secteur', fontsize=12)
    ax2.set_title(f'Changement cumulé de prix par secteur - {current_date.strftime("%Y-%m-%d")}',
                  fontsize=14, fontweight='bold')
    ax2.axvline(0, color='black', linestyle='--', alpha=0.3)
    plt.tight_layout()

anim2 = animation.FuncAnimation(fig2, animate_sector_change, frames=len(sampled_dates_sec),
                                interval=100, repeat=True)

print("Création de l'animation 2...")
anim2.save(os.path.join(output_dir, 'sp500_sector_change.gif'), writer='pillow', fps=10)
plt.close()

print("Animation 2 créée : sp500_sector_change.gif")
HTML(anim2.to_jshtml())

Création de l'animation 2...
Animation 2 créée : sp500_sector_change.gif


<Figure size 640x480 with 0 Axes>

## ANIMATION 3 : Classement des Top 5 stocks

In [18]:
# Préparer les données de classement
ranking_data = sp500_data.sort_values('date').copy()
ranking_data['rank'] = ranking_data.groupby('date')['close'].rank(ascending=False, method='first')
ranking_data = ranking_data[ranking_data['rank'] <= 5]
ranking_data = ranking_data.sort_values(['date', 'rank'])

# Échantillonner les dates
unique_dates_rank = sorted(ranking_data['date'].unique())
sampled_dates_rank = unique_dates_rank[::7]

fig3, ax3 = plt.subplots(figsize=(12, 6))

def animate_top5_ranking(frame):
    ax3.clear()
    current_date = sampled_dates_rank[frame]
    data_at_date = ranking_data[ranking_data['date'] == current_date].sort_values('rank', ascending=False)
    
    sectors = data_at_date['sector'].values
    colors_map = {'Technology': '#8dd3c7', 'Consumer': '#ffffb3', 'Finance': '#bebada',
                  'Healthcare': '#fb8072', 'Industrial': '#80b1d3', 'Energy': '#fdb462'}
    colors = [colors_map.get(s, '#b3de69') for s in sectors]
    
    y_pos = np.arange(len(data_at_date))
    ax3.barh(y_pos, data_at_date['close'], color=colors, alpha=0.8)
    ax3.set_yticks(y_pos)
    ax3.set_yticklabels(data_at_date['symbol'], fontweight='bold')
    ax3.set_xlabel('Prix (USD)', fontsize=12)
    ax3.set_ylabel('Rang', fontsize=12)
    ax3.set_title(f'Top 5 Actions par prix - {current_date.strftime("%Y-%m-%d")}',
                  fontsize=14, fontweight='bold')
    
    # Ajouter les labels des symboles sur les barres
    for i, (idx, row) in enumerate(data_at_date.iterrows()):
        ax3.text(row['close'] + 5, i, row['symbol'], va='center', fontweight='bold')
    
    plt.tight_layout()

anim3 = animation.FuncAnimation(fig3, animate_top5_ranking, frames=len(sampled_dates_rank),
                                interval=100, repeat=True)

print("Création de l'animation 3...")
anim3.save(os.path.join(output_dir, 'sp500_top5_ranking.gif'), writer='pillow', fps=10)
plt.close()

print("Animation 3 créée : sp500_top5_ranking.gif")
HTML(anim3.to_jshtml())

Création de l'animation 3...
Animation 3 créée : sp500_top5_ranking.gif


<Figure size 640x480 with 0 Axes>

In [19]:
print("\n✓ Partie 4 complétée : 3 animations créées")
print("  - sp500_price_evolution.gif")
print("  - sp500_sector_change.gif")
print("  - sp500_top5_ranking.gif")
print(f"\nFichiers sauvegardés dans : {output_dir}")


✓ Partie 4 complétée : 3 animations créées
  - sp500_price_evolution.gif
  - sp500_sector_change.gif
  - sp500_top5_ranking.gif

Fichiers sauvegardés dans : C:\Users\USER\Desktop\bachelor-3-ece\Visualisation\TP6\sp500_python
